# NLP Basic Assignment
## 과제 : spam.csv를 활용하여 유의미한 해석을 도출해주세요!

In [1]:
import pandas as pd
import warnings

warnings.filterwarnings(action='ignore') 

## Load Data
- 보시면 아시다시피 spam.csv는 라벨이 있는 데이터입니다.
- 7주차 주제가 텍스트 기초인만큼 텍스트만 활용하셔도 되고 라벨까지 활용하셔서 모델을 돌려보셔도 좋습니다.

In [2]:
df = pd.read_csv('spam.csv')

In [3]:
df.iloc[5]['v2']

"FreeMsg Hey there darling it's been 3 week's now and no word back! I'd like some fun you up for it still? Tb ok! XxX std chgs to send, å£1.50 to rcv"

In [4]:
df.columns

Index(['v1', 'v2'], dtype='object')

## Tokenizing

In [5]:
import nltk

In [6]:
from nltk.tokenize import word_tokenize

# 토큰화 함수
def tokenize_text(text):
    return word_tokenize(text.lower())

In [7]:
# 토큰화 적용
df['tokenized'] = df['v2'].apply(tokenize_text)

# 토큰화 및 lower 결과 확인
df.head()

v1                                                 v2  \
0   ham  Go until jurong point, crazy.. Available only ...   
1   ham                      Ok lar... Joking wif u oni...   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3   ham  U dun say so early hor... U c already then say...   
4   ham  Nah I don't think he goes to usf, he lives aro...   

                                           tokenized  
0  [go, until, jurong, point, ,, crazy, .., avail...  
1           [ok, lar, ..., joking, wif, u, oni, ...]  
2  [free, entry, in, 2, a, wkly, comp, to, win, f...  
3  [u, dun, say, so, early, hor, ..., u, c, alrea...  
4  [nah, i, do, n't, think, he, goes, to, usf, ,,...

In [8]:
len(df)

5572

## Embedding

- 수업에서 다룬 임베딩 방법에는 One-hot encoding, CBOW, Skip-gram 등이 있었습니다. 다양한 시도와 '비교' 결과를 함께 적어주세요! 파라미터를 조정해가는 과정도 해석에 도움이 될 수 있겠죠 :)

In [9]:
from collections import Counter

# 모든 토큰을 하나의 리스트로 합치기
all_tokens = [token for sublist in df['tokenized'].tolist() for token in sublist]

# 가장 빈번하게 등장하는 단어 1000개를 선택 (성능과 시간을 고려)
most_common_tokens = [item[0] for item in Counter(all_tokens).most_common(1000)]
print('len(most_common_tokens):',len(most_common_tokens))

len(most_common_tokens): 1000


### One-hot encoding

In [10]:
from sklearn.preprocessing import OneHotEncoder
import numpy as np

one_hot_encoder = OneHotEncoder(sparse=False)
one_hot_encoded = one_hot_encoder.fit_transform(np.array(most_common_tokens).reshape(-1, 1))
one_hot_encoded

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [11]:
# One-Hot Encoding을 위한 딕셔너리 생성
token_to_one_hot = {token: one_hot for token, one_hot in zip(most_common_tokens, one_hot_encoded)}

# One-Hot Encoding 예시
def one_hot_encode_sentence(sentence):
    return np.sum([token_to_one_hot.get(token, np.zeros_like(one_hot_encoded[0])) for token in sentence], axis=0)

df['one_hot_encoded'] = df['tokenized'].apply(one_hot_encode_sentence)
df.head()

v1                                                 v2  \
0   ham  Go until jurong point, crazy.. Available only ...   
1   ham                      Ok lar... Joking wif u oni...   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3   ham  U dun say so early hor... U c already then say...   
4   ham  Nah I don't think he goes to usf, he lives aro...   

                                           tokenized  \
0  [go, until, jurong, point, ,, crazy, .., avail...   
1           [ok, lar, ..., joking, wif, u, oni, ...]   
2  [free, entry, in, 2, a, wkly, comp, to, win, f...   
3  [u, dun, say, so, early, hor, ..., u, c, alrea...   
4  [nah, i, do, n't, think, he, goes, to, usf, ,,...   

                                     one_hot_encoded  
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
2  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...

### CBOW

In [12]:
from gensim.models import Word2Vec

# CBOW 모델 학습
# sg=0
cbow_model = Word2Vec(sentences=df['tokenized'].tolist(), vector_size=100, window=5, min_count=1, sg=0)

In [13]:
def cbow_encode_sentence(sentence):
    return np.mean([cbow_model.wv[token] for token in sentence if token in cbow_model.wv.index_to_key], axis=0)

df['cbow_encoded'] = df['tokenized'].apply(cbow_encode_sentence)
df.head()

v1                                                 v2  \
0   ham  Go until jurong point, crazy.. Available only ...   
1   ham                      Ok lar... Joking wif u oni...   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3   ham  U dun say so early hor... U c already then say...   
4   ham  Nah I don't think he goes to usf, he lives aro...   

                                           tokenized  \
0  [go, until, jurong, point, ,, crazy, .., avail...   
1           [ok, lar, ..., joking, wif, u, oni, ...]   
2  [free, entry, in, 2, a, wkly, comp, to, win, f...   
3  [u, dun, say, so, early, hor, ..., u, c, alrea...   
4  [nah, i, do, n't, think, he, goes, to, usf, ,,...   

                                     one_hot_encoded  \
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                        cbow_encoded  
0  [-0.193904, 0.49288055, 0.07849371, 0.08804812...  
1  [-0.25311583, 0.62983596, -0.011074761, 0.0478...  
2  [-0.13027483, 0.32703727, 0.21637887, 0.143397...  
3  [-0.2840665, 0.7431661, 0.012164412, 0.0619966...  
4  [-0.22082081, 0.74617964, -0.040470585, 0.0404...

### Skip-gram

In [14]:
# Skip-gram 모델 학습
# sg=1
skip_gram_model = Word2Vec(sentences=df['tokenized'].tolist(), vector_size=100, window=5, min_count=1, sg=1)

In [15]:
def skip_gram_encode_sentence(sentence):
    return np.mean([skip_gram_model.wv[token] for token in sentence if token in skip_gram_model.wv.index_to_key], axis=0)

df['skip_gram_encoded'] = df['tokenized'].apply(skip_gram_encode_sentence)
df.head()

v1                                                 v2  \
0   ham  Go until jurong point, crazy.. Available only ...   
1   ham                      Ok lar... Joking wif u oni...   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3   ham  U dun say so early hor... U c already then say...   
4   ham  Nah I don't think he goes to usf, he lives aro...   

                                           tokenized  \
0  [go, until, jurong, point, ,, crazy, .., avail...   
1           [ok, lar, ..., joking, wif, u, oni, ...]   
2  [free, entry, in, 2, a, wkly, comp, to, win, f...   
3  [u, dun, say, so, early, hor, ..., u, c, alrea...   
4  [nah, i, do, n't, think, he, goes, to, usf, ,,...   

                                     one_hot_encoded  \
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                        cbow_encoded  \
0  [-0.193904, 0.49288055, 0.07849371, 0.08804812...   
1  [-0.25311583, 0.62983596, -0.011074761, 0.0478...   
2  [-0.13027483, 0.32703727, 0.21637887, 0.143397...   
3  [-0.2840665, 0.7431661, 0.012164412, 0.0619966...   
4  [-0.22082081, 0.74617964, -0.040470585, 0.0404...   

                                   skip_gram_encoded  
0  [-0.09179774, 0.35971078, -0.009870422, 0.0357...  
1  [-0.16784742, 0.4579163, -0.063962586, -0.0124...  
2  [0.096640505, 0.14322801, 0.052255377, 0.08483...  
3  [-0.15043844, 0.48421115, -0.09558928, -0.0650...  
4  [-0.009346407, 0.43039858, -0.015610164, 0.046...

### 각 임베딩 방식 비교

#### One-hot Encoding
- One-hot encoding은 단어를 고차원의 벡터로 표현합니다. 벡터의 크기는 단어 사전의 크기와 동일하며, 각 단어는 단어 사전에서의 위치에 해당하는 인덱스에 1의 값을 갖습니다.

#### CBOW
- BOW는 단어를 주변 단어를 통해 예측하는 방식으로 작동합니다. 각 단어는 실수 벡터로 표현되며, 벡터의 차원은 설정에 따라 다릅니다. 여기서는 100차원을 사용했습니다.

#### Skip-gram

- Skip-gram은 주변 단어를 중심 단어를 통해 예측하는 방식으로 작동합니다. CBOW와 마찬가지로 각 단어는 실수 벡터로 표현됩니다.

#### 비교
- One-hot encoding은 단어 간의 관계나 의미를 고려하지 않습니다. 이는 메모리를 많이 사용하고, 단어의 의미나 문맥을 파악하는 데 한계가 있습니다.
- CBOW와 Skip-gram은 단어의 문맥을 고려하여 단어를 임베딩합니다. 이는 단어 간의 유사성을 파악하는 데 유용합니다.
- 파라미터 조정
    - vector_size: 단어 벡터의 차원 수. 더 높은 차원은 더 많은 정보를 담을 수 있지만, 계산 비용이 증가합니다.
    - window: 고려할 주변 단어의 범위. 더 큰 윈도우는 더 많은 문맥을 고려합니다.
    - min_count: 모델 학습에 사용할 최소 단어 빈도. 너무 낮게 설정하면 희귀한 단어 때문에 모델 성능이 떨어질 수 있습니다.

## 본인이 도출해낸 해석을 적어주세요!

- 유사도, Wordcloud, 이진 분류 모델, Plot 뭐든 상관없으니 분명하고 인상적인 해석을 적어주시면 됩니다.

In [16]:
from sklearn.manifold import TSNE
import plotly.express as px

# One-Hot Encoding 데이터
one_hot_data = np.array(df['one_hot_encoded'].tolist())

# CBOW 데이터
cbow_data = np.array(df['cbow_encoded'].tolist())

# Skip-gram 데이터
skip_gram_data = np.array(df['skip_gram_encoded'].tolist())

# t-SNE 모델 생성 및 학습 for 3D
tsne_3d = TSNE(n_components=3, random_state=0)

one_hot_3d = tsne_3d.fit_transform(one_hot_data)
cbow_3d = tsne_3d.fit_transform(cbow_data)
skip_gram_3d = tsne_3d.fit_transform(skip_gram_data)

In [17]:
# One-Hot Encoding -> label에 따라 시각화해본 결과, 임베딩에서는 두 데이터가 눈에 띄게 분리되어 보이지 않음.
df_one_hot_3d = pd.DataFrame(one_hot_3d, columns=['x', 'y', 'z'])
df_one_hot_3d['label'] = df['v1']

fig = px.scatter_3d(df_one_hot_3d, x='x', y='y', z='z', color='label', title="One-Hot Encoding")
fig.update_traces(marker=dict(size=1))
fig.update_layout(scene=dict(aspectmode="cube", aspectratio=dict(x=1, y=1, z=1)))
fig.show()
fig.write_html("One_Hot_Encoding.html")

<div style="text-align: center;">
    <img src="./img/One_Hot_Encoding.png" width="1000"/><br>
</div>

In [18]:
# CBOW -> label에 따라 시각화해본 결과,One-Hot Encoding에 비해 label에 따른 임베딩 결과가 유의미해 보임.
df_cbow_3d = pd.DataFrame(cbow_3d, columns=['x', 'y', 'z'])
df_cbow_3d['label'] = df['v1']

fig = px.scatter_3d(df_cbow_3d, x='x', y='y', z='z', color='label', title="CBOW")
fig.update_traces(marker=dict(size=1))
fig.update_layout(scene=dict(aspectmode="cube", aspectratio=dict(x=1, y=1, z=1)))
fig.show()
fig.write_html("CBOW.html")

<div style="text-align: center;">
    <img src="./img/CBOW.png" width="1000"/><br>
</div>

In [19]:
# Skip-gram 시각화 -> label에 따라 시각화해본 결과, 3 방식 중 가장 임베딩에서 label이 잘 분리되어 있음을 보임
df_skip_gram_3d = pd.DataFrame(skip_gram_3d, columns=['x', 'y', 'z'])
df_skip_gram_3d['label'] = df['v1']

fig = px.scatter_3d(df_skip_gram_3d, x='x', y='y', z='z', color='label', title="Skip-gram")
fig.update_traces(marker=dict(size=1))
fig.update_layout(scene=dict(aspectmode="cube", aspectratio=dict(x=1, y=1, z=1)))
fig.show()
fig.write_html("Skip-gram.html")

<div style="text-align: center;">
    <img src="./img/Skip_Gram.png" width="1000"/><br>
</div>

In [21]:
import plotly.graph_objs as go
## 3가지 임베딩 방식을 하나의 plot에 띄운 결과
## skip-gram의 임베딩한 값들의 거리가 제일 가깝고, 다음으로 One-Hot Encoding, CBOW 순서였음
## 이 시각화 결과물을 바탕으로 같은 분류 모델을 사용했을 때, 유의미한 차이가 있을 것이라 기대함

# 새로운 fig 생성
fig = go.Figure()

# One-Hot Encoding 데이터 추가
fig.add_trace(go.Scatter3d(x=df_one_hot_3d['x'], y=df_one_hot_3d['y'], z=df_one_hot_3d['z'],
                           mode='markers', marker=dict(size=2, color='red'),
                           name='One-Hot Encoding'))

# CBOW 데이터 추가
fig.add_trace(go.Scatter3d(x=df_cbow_3d['x'], y=df_cbow_3d['y'], z=df_cbow_3d['z'],
                           mode='markers', marker=dict(size=2, color='green'),
                           name='CBOW'))

# Skip-gram 데이터 추가
fig.add_trace(go.Scatter3d(x=df_skip_gram_3d['x'], y=df_skip_gram_3d['y'], z=df_skip_gram_3d['z'],
                           mode='markers', marker=dict(size=2, color='blue'),
                           name='Skip-gram'))

# Layout 설정
fig.update_layout(scene=dict(aspectmode="cube", aspectratio=dict(x=1, y=1, z=1)),
                  title="Embedding Comparison in a Single Plot")

# 그래프 출력
fig.show()
fig.write_html("Embedding Comparison.html")

<div style="text-align: center;">
    <img src="./img/Comparison.png" width="1000"/><br>
</div>

## 이진분류(XGBoost Classifier)

In [22]:
df.head()

v1                                                 v2  \
0   ham  Go until jurong point, crazy.. Available only ...   
1   ham                      Ok lar... Joking wif u oni...   
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...   
3   ham  U dun say so early hor... U c already then say...   
4   ham  Nah I don't think he goes to usf, he lives aro...   

                                           tokenized  \
0  [go, until, jurong, point, ,, crazy, .., avail...   
1           [ok, lar, ..., joking, wif, u, oni, ...]   
2  [free, entry, in, 2, a, wkly, comp, to, win, f...   
3  [u, dun, say, so, early, hor, ..., u, c, alrea...   
4  [nah, i, do, n't, think, he, goes, to, usf, ,,...   

                                     one_hot_encoded  \
0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2  [0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                        cbow_encoded  \
0  [-0.193904, 0.49288055, 0.07849371, 0.08804812...   
1  [-0.25311583, 0.62983596, -0.011074761, 0.0478...   
2  [-0.13027483, 0.32703727, 0.21637887, 0.143397...   
3  [-0.2840665, 0.7431661, 0.012164412, 0.0619966...   
4  [-0.22082081, 0.74617964, -0.040470585, 0.0404...   

                                   skip_gram_encoded  
0  [-0.09179774, 0.35971078, -0.009870422, 0.0357...  
1  [-0.16784742, 0.4579163, -0.063962586, -0.0124...  
2  [0.096640505, 0.14322801, 0.052255377, 0.08483...  
3  [-0.15043844, 0.48421115, -0.09558928, -0.0650...  
4  [-0.009346407, 0.43039858, -0.015610164, 0.046...

In [23]:
from sklearn.model_selection import train_test_split
from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score, classification_report
import pandas as pd

# 랜덤 시드 설정
random_seed = 42

# 데이터를 train, valid, test로 나누기 (0.6, 0.2, 0.2)
df_train, df_temp = train_test_split(df, test_size=0.4, random_state=random_seed)
df_valid, df_test = train_test_split(df_temp, test_size=0.5, random_state=random_seed)

# XGBoost 분류기 초기화
xgb_clf = XGBClassifier()

# 결과를 저장할 데이터프레임 초기화
result_df = pd.DataFrame(columns=['Embedding', 'Accuracy'])

In [24]:
# One-Hot Encoding으로 분류 모델 학습 및 평가
X_train_one_hot = np.stack(df_train['one_hot_encoded'].to_numpy())
y_train_one_hot = df_train['v1'].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

X_valid_one_hot = np.stack(df_valid['one_hot_encoded'].to_numpy())
y_valid_one_hot = df_valid['v1'].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

xgb_clf.fit(X_train_one_hot, y_train_one_hot)
y_pred_one_hot = xgb_clf.predict(X_valid_one_hot)
accuracy_one_hot = accuracy_score(y_valid_one_hot, y_pred_one_hot)

result_df = result_df.append({'Embedding': 'One-Hot', 'Accuracy': accuracy_one_hot}, ignore_index=True)

In [25]:
# CBOW로 분류 모델 학습 및 평가
X_train_cbow = np.stack(df_train['cbow_encoded'].dropna().to_numpy())
y_train_cbow = df_train['v1'].loc[df_train['cbow_encoded'].dropna().index].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

X_valid_cbow = np.stack(df_valid['cbow_encoded'].dropna().to_numpy())
y_valid_cbow = df_valid['v1'].loc[df_valid['cbow_encoded'].dropna().index].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

xgb_clf.fit(X_train_cbow, y_train_cbow)
y_pred_cbow = xgb_clf.predict(X_valid_cbow)
accuracy_cbow = accuracy_score(y_valid_cbow, y_pred_cbow)

result_df = result_df.append({'Embedding': 'CBOW', 'Accuracy': accuracy_cbow}, ignore_index=True)

In [26]:
# Skip-gram으로 분류 모델 학습 및 평가
X_train_skip_gram = np.stack(df_train['skip_gram_encoded'].dropna().to_numpy())
y_train_skip_gram = df_train['v1'].loc[df_train['skip_gram_encoded'].dropna().index].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

X_valid_skip_gram = np.stack(df_valid['skip_gram_encoded'].dropna().to_numpy())
y_valid_skip_gram = df_valid['v1'].loc[df_valid['skip_gram_encoded'].dropna().index].apply(lambda x: 1 if x == 'spam' else 0).to_numpy()

xgb_clf.fit(X_train_skip_gram, y_train_skip_gram)
y_pred_skip_gram = xgb_clf.predict(X_valid_skip_gram)
accuracy_skip_gram = accuracy_score(y_valid_skip_gram, y_pred_skip_gram)

result_df = result_df.append({'Embedding': 'Skip-gram', 'Accuracy': accuracy_skip_gram}, ignore_index=True)

In [27]:
result_df

Embedding  Accuracy
0    One-Hot  0.974865
1       CBOW  0.962298
2  Skip-gram  0.981149

## 결과 해석

1. One-Hot Encoding: 정확도가 약 97.5%로 매우 높습니다. 하지만 이 방법은 단어 간의 관계나 문맥을 고려하지 않습니다. 단순히 단어의 존재 여부만을 표현하기 때문에, 모델이 고차원적인 특성을 학습하기 어려울 수 있습니다.

2. CBOW (Continuous Bag of Words): 정확도가 약 96.2%로, One-Hot Encoding보다는 약간 낮습니다. CBOW는 단어의 문맥을 고려하기 때문에 더 복잡한 특성을 학습할 수 있습니다. 그러나 이 경우에는 그 복잡성이 큰 이점으로 작용하지 않은 것 같습니다.

3. Skip-gram: 정확도가 약 98.1%로 가장 높습니다. Skip-gram은 CBOW와 달리 주어진 단어를 기반으로 문맥 내의 단어를 예측하는 방식으로 학습합니다. 이렇게 되면 단어의 의미를 더 잘 파악할 수 있어, 더 복잡하고 다양한 특성을 학습할 수 있습니다.

## 개인적인 생각

- 차원의 저주: One-Hot Encoding은 차원이 매우 높아질 수 있고, 이는 모델이 과적합될 수 있지만 현케이스에서는 아니었습니다.

- 문맥 정보: CBOW와 Skip-gram은 문맥 정보를 사용하기 때문에, 단어의 의미를 더 정확하게 파악할 수 있습니다. 이러한 이유로 Skip-gram이 가장 높은 성능을 보였을 것입니다.

- 데이터 불균형: 스팸과 햄(일반 메시지)의 비율에 따라서도 성능이 달라질 수 있습니다. 여기서는 모든 모델이 높은 성능을 보이고 있어, 데이터 불균형은 큰 영향을 미치지 않은 것으로 보입니다.

- 모델 복잡성: One-Hot Encoding은 가장 단순한 형태의 임베딩이기 때문에, 모델이 빠르게 학습됩니다. 반면, CBOW와 Skip-gram은 복잡한 특성을 학습할 수 있지만, 이로 인해 성능이 떨어질 수도 있습니다. 이 경우에는 Skip-gram이 가장 복잡한 특성을 잘 학습하여 높은 성능을 보였습니다.

## 결론

- 시각화 결과물을 봤을 때, 거리가 가장 멀리 떨어진 One-Hot Encoding 방식이 제일 성능이 좋을 것으로 예상했으나<br>반대로 두 번째로 임베딩된 벡터 거리가 가까운 Skip-gram의 성능이 가장 뛰어났습니다.
- 현재 데이터셋만 보고 단정짓기에는 어렵지만, 데이터셋이 복잡해질수록 Skip-gram이나 CBOW방식이 더 성능이 One-Hot Encoding 대비 좋아질 것으로 생각됩니다.
- 혹은 One-Hot Encoding에서 sparse=False라는 파라미터를 통해 희소벡터를 밀집배열로 변환해서 그런 것인가 생각을 했지만,<br>간단하게 찾아보니 분류 결과에는 영향을 끼치지 않고 단순히 연산 속도와 관련된 부분과 관련이 있었습니다.
- 그리고 XGBoost는 거의 간단한 데이터셋에서는 만능이기에, 다른 모델들을 통해 추가적인 실험을 진행할 필요성이 있다고 판단됩니다.